In [1]:
#pip install arcgis

In [2]:
from arcgis.gis import GIS
from arcgis.geocoding import batch_geocode

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [3]:
url = 'https://en.wikipedia.org/wiki/List_of_neighbourhoods_in_Calgary'
data = pd.read_html(url)
calgary_data = data[0]

In [4]:
calgary_data.columns = ['Neighborhood', 'Quadrant', 'Sector', 'Ward', 'Type',
       '2012 PopulationRank', 'Population(2012)', 'Population(2011)',
       '% change', 'Dwellings(2012)', 'Area(km2)', 'Populationdensity']
calgary_data = calgary_data.dropna(subset=['Area(km2)'])
calgary_data.reset_index(drop=True, inplace=True)


In [5]:
calgary_data = calgary_data.drop(calgary_data[(calgary_data.Neighborhood == 'Total City of Calgary')].index)
calgary_data.reset_index(drop=True, inplace=True)
calgary_data

Neighborhood Quadrant     Sector      Ward         Type  \
0                        Abbeydale    NE/SE  Northeast        10  Residential   
1                           Acadia       SE      South         9  Residential   
2     Albert Park/Radisson Heights       SE       East        10  Residential   
3                         Altadore       SW     Centre        11  Residential   
4                 Alyth/Bonnybrook       SE     Centre         9   Industrial   
5                   Applewood Park    SE/NE       East        10  Residential   
6                      Arbour Lake       NW  Northwest         2  Residential   
7                      Aspen Woods       SW       West         6  Residential   
8                       Auburn Bay       SE  Southeast        12  Residential   
9             Aurora Business Park       NE      North         3   Industrial   
10                     Banff Trail       NW     Centre         7  Residential   
11                        Bankview       SW     Centre         8  Residential   
12                         Bayview       SW      South        11  Residential   
13              Beddington Heights    NW/NE      North         4  Residential   
14                        Bel-Aire       SW     Centre        11  Residential   
15                        Beltline    SW/SE     Centre         8  Residential   
16                 Bonavista Downs       SE      South        14  Residential   
17                         Bowness       NW  Northwest         1  Residential   
18                        Braeside       SW      South        11  Residential   
19                       Brentwood       NW  Northwest         7  Residential   
20            Bridgeland/Riverside    NE/SE     Centre       7/9  Residential   
21                      Bridlewood       SW      South        13  Residential   
22                       Britannia       SW     Centre        11  Residential   
23                Burns Industrial       SE     Centre         9   Industrial   
24   Calgary International Airport       NE  Northeast         3   Industrial   
25                Cambrian Heights       NW     Centre         7  Residential   
26             Canada Olympic Park       SW       West         1   Major Park   
27                  Canyon Meadows       SW      South        13  Residential   
28                    Capitol Hill       NW     Centre         7  Residential   
29                     Castleridge       NE  Northeast         5  Residential   
30                       Cedarbrae       SW      South        11  Residential   
31                      CFB Currie       SW       West        11  Residential   
32            CFB Lincoln Park PMQ       SW       West        11  Residential   
33                       Chaparral       SE      South        14  Residential   
34                     Charleswood       NW  Northwest         7  Residential   
35                       Chinatown    SW/SE     Centre         7  Residential   
36                    Chinook Park       SW      South        11  Residential   
37                   Christie Park       SW       West         6  Residential   
38                         Citadel       NW  Northwest         2  Residential   
39                  Cliff Bungalow       SW     Centre         8  Residential   
40                      Coach Hill       SW       West         6  Residential   
41                     Collingwood       NW  Northwest         7  Residential   
42                     Copperfield       SE  Southeast        12  Residential   
43                   Coral Springs       NE  Northeast         5  Residential   
44                    Cougar Ridge       SW       West         6  Residential   
45                   Country Hills       NW      North         4  Residential   
46           Country Hills Village       NE      North         3  Residential   
47                  Coventry Hills       NE      North         3  Residential   
48                        Cranston       SE  Southeas

In [6]:
calgary_res = calgary_data[calgary_data['Type'] == 'Residential'].reset_index(drop=True)
calgary_res

Neighborhood Quadrant     Sector  Ward         Type  \
0                        Abbeydale    NE/SE  Northeast    10  Residential   
1                           Acadia       SE      South     9  Residential   
2     Albert Park/Radisson Heights       SE       East    10  Residential   
3                         Altadore       SW     Centre    11  Residential   
4                   Applewood Park    SE/NE       East    10  Residential   
5                      Arbour Lake       NW  Northwest     2  Residential   
6                      Aspen Woods       SW       West     6  Residential   
7                       Auburn Bay       SE  Southeast    12  Residential   
8                      Banff Trail       NW     Centre     7  Residential   
9                         Bankview       SW     Centre     8  Residential   
10                         Bayview       SW      South    11  Residential   
11              Beddington Heights    NW/NE      North     4  Residential   
12                        Bel-Aire       SW     Centre    11  Residential   
13                        Beltline    SW/SE     Centre     8  Residential   
14                 Bonavista Downs       SE      South    14  Residential   
15                         Bowness       NW  Northwest     1  Residential   
16                        Braeside       SW      South    11  Residential   
17                       Brentwood       NW  Northwest     7  Residential   
18            Bridgeland/Riverside    NE/SE     Centre   7/9  Residential   
19                      Bridlewood       SW      South    13  Residential   
20                       Britannia       SW     Centre    11  Residential   
21                Cambrian Heights       NW     Centre     7  Residential   
22                  Canyon Meadows       SW      South    13  Residential   
23                    Capitol Hill       NW     Centre     7  Residential   
24                     Castleridge       NE  Northeast     5  Residential   
25                       Cedarbrae       SW      South    11  Residential   
26                      CFB Currie       SW       West    11  Residential   
27            CFB Lincoln Park PMQ       SW       West    11  Residential   
28                       Chaparral       SE      South    14  Residential   
29                     Charleswood       NW  Northwest     7  Residential   
30                       Chinatown    SW/SE     Centre     7  Residential   
31                    Chinook Park       SW      South    11  Residential   
32                   Christie Park       SW       West     6  Residential   
33                         Citadel       NW  Northwest     2  Residential   
34                  Cliff Bungalow       SW     Centre     8  Residential   
35                      Coach Hill       SW       West     6  Residential   
36                     Collingwood       NW  Northwest     7  Residential   
37                     Copperfield       SE  Southeast    12  Residential   
38                   Coral Springs       NE  Northeast     5  Residential   
39                    Cougar Ridge       SW       West     6  Residential   
40                   Country Hills       NW      North     4  Residential   
41           Country Hills Village       NE      North     3  Residential   
42                  Coventry Hills       NE      North     3  Residential   
43                        Cranston       SE  Southeast    12  Residential   
44                Crescent Heights    NE/NW     Centre     7  Residential   
45                       Crestmont       SW       West     1  Residential   
46                       Dalhousie       NW  Northwest     7  Residential   
47                      Deer Ridge       SE      South    14  Residential   
48                        Deer Run       SE      South    14  Residential   
49                    Diamond Cove       SE      South    14  Residential   
50                 Discovery Ridge       SW       West     6  Residential   
51                

In [7]:
gis = GIS("http://arcgis.com", "farazamalik", "Faraz@34")

In [8]:
addresses = (calgary_res['Neighborhood'] + ', Calgary, Alberta')
addresses

0                          Abbeydale, Calgary, Alberta
1                             Acadia, Calgary, Alberta
2       Albert Park/Radisson Heights, Calgary, Alberta
3                           Altadore, Calgary, Alberta
4                     Applewood Park, Calgary, Alberta
5                        Arbour Lake, Calgary, Alberta
6                        Aspen Woods, Calgary, Alberta
7                         Auburn Bay, Calgary, Alberta
8                        Banff Trail, Calgary, Alberta
9                           Bankview, Calgary, Alberta
10                           Bayview, Calgary, Alberta
11                Beddington Heights, Calgary, Alberta
12                          Bel-Aire, Calgary, Alberta
13                          Beltline, Calgary, Alberta
14                   Bonavista Downs, Calgary, Alberta
15                           Bowness, Calgary, Alberta
16                          Braeside, Calgary, Alberta
17                         Brentwood, Calgary, Alberta
18        

In [9]:
results = batch_geocode(addresses)
results

[{'address': 'Abbeydale, Calgary, Alberta',
  'location': {'x': -113.92545999999999, 'y': 51.05976000000004},
  'score': 100,
  'attributes': {'ResultID': 0,
   'Loc_name': 'World',
   'Status': 'M',
   'Score': 100,
   'Match_addr': 'Abbeydale, Calgary, Alberta',
   'LongLabel': 'Abbeydale, Calgary, Alberta, CAN',
   'ShortLabel': 'Abbeydale',
   'Addr_type': 'Locality',
   'Type': 'Neighborhood',
   'PlaceName': 'Abbeydale',
   'Place_addr': 'Calgary, Alberta',
   'Phone': '',
   'URL': '',
   'Rank': 15,
   'AddBldg': '',
   'AddNum': '',
   'AddNumFrom': '',
   'AddNumTo': '',
   'AddRange': '',
   'Side': '',
   'StPreDir': '',
   'StPreType': '',
   'StName': '',
   'StType': '',
   'StDir': '',
   'BldgType': '',
   'BldgName': '',
   'LevelType': '',
   'LevelName': '',
   'UnitType': '',
   'UnitName': '',
   'SubAddr': '',
   'StAddr': '',
   'Block': '',
   'Sector': '',
   'Nbrhd': 'Abbeydale',
   'District': 'Calgary',
   'City': 'Calgary',
   'MetroArea': 'Calgary Metro A

In [10]:
latcoords = []
longcoords = []

for coordinates in results:
    latitude='{:.6f}'.format( float(coordinates['location']['y']))
    longitude='{:.6f}'.format( float(coordinates['location']['x']))
    latcoords.append(latitude)
    longcoords.append(longitude)

In [11]:
calgary_res['Latitude'] = latcoords
calgary_res['Longitude'] = longcoords
calgary_res.reset_index(drop=True, inplace=True)
calgary_res

Neighborhood Quadrant     Sector  Ward         Type  \
0                        Abbeydale    NE/SE  Northeast    10  Residential   
1                           Acadia       SE      South     9  Residential   
2     Albert Park/Radisson Heights       SE       East    10  Residential   
3                         Altadore       SW     Centre    11  Residential   
4                   Applewood Park    SE/NE       East    10  Residential   
5                      Arbour Lake       NW  Northwest     2  Residential   
6                      Aspen Woods       SW       West     6  Residential   
7                       Auburn Bay       SE  Southeast    12  Residential   
8                      Banff Trail       NW     Centre     7  Residential   
9                         Bankview       SW     Centre     8  Residential   
10                         Bayview       SW      South    11  Residential   
11              Beddington Heights    NW/NE      North     4  Residential   
12                        Bel-Aire       SW     Centre    11  Residential   
13                        Beltline    SW/SE     Centre     8  Residential   
14                 Bonavista Downs       SE      South    14  Residential   
15                         Bowness       NW  Northwest     1  Residential   
16                        Braeside       SW      South    11  Residential   
17                       Brentwood       NW  Northwest     7  Residential   
18            Bridgeland/Riverside    NE/SE     Centre   7/9  Residential   
19                      Bridlewood       SW      South    13  Residential   
20                       Britannia       SW     Centre    11  Residential   
21                Cambrian Heights       NW     Centre     7  Residential   
22                  Canyon Meadows       SW      South    13  Residential   
23                    Capitol Hill       NW     Centre     7  Residential   
24                     Castleridge       NE  Northeast     5  Residential   
25                       Cedarbrae       SW      South    11  Residential   
26                      CFB Currie       SW       West    11  Residential   
27            CFB Lincoln Park PMQ       SW       West    11  Residential   
28                       Chaparral       SE      South    14  Residential   
29                     Charleswood       NW  Northwest     7  Residential   
30                       Chinatown    SW/SE     Centre     7  Residential   
31                    Chinook Park       SW      South    11  Residential   
32                   Christie Park       SW       West     6  Residential   
33                         Citadel       NW  Northwest     2  Residential   
34                  Cliff Bungalow       SW     Centre     8  Residential   
35                      Coach Hill       SW       West     6  Residential   
36                     Collingwood       NW  Northwest     7  Residential   
37                     Copperfield       SE  Southeast    12  Residential   
38                   Coral Springs       NE  Northeast     5  Residential   
39                    Cougar Ridge       SW       West     6  Residential   
40                   Country Hills       NW      North     4  Residential   
41           Country Hills Village       NE      North     3  Residential   
42                  Coventry Hills       NE      North     3  Residential   
43                        Cranston       SE  Southeast    12  Residential   
44                Crescent Heights    NE/NW     Centre     7  Residential   
45                       Crestmont       SW       West     1  Residential   
46                       Dalhousie       NW  Northwest     7  Residential   
47                      Deer Ridge       SE      South    14  Residential   
48                        Deer Run       SE      South    14  Residential   
49                    Diamond Cove       SE      South    14  Residential   
50                 Discovery Ridge       SW       West     6  Residential   
51                

In [12]:
calgary_res.dtypes

Neighborhood            object
Quadrant                object
Sector                  object
Ward                    object
Type                    object
2012 PopulationRank     object
Population(2012)       float64
Population(2011)       float64
% change                object
Dwellings(2012)        float64
Area(km2)              float64
Populationdensity       object
Latitude                object
Longitude               object
dtype: object

In [13]:
calgary_res[["Latitude", "Longitude"]] = calgary_res[["Latitude", "Longitude"]].astype("float")

In [14]:
calgary_res.dtypes

Neighborhood            object
Quadrant                object
Sector                  object
Ward                    object
Type                    object
2012 PopulationRank     object
Population(2012)       float64
Population(2011)       float64
% change                object
Dwellings(2012)        float64
Area(km2)              float64
Populationdensity       object
Latitude               float64
Longitude              float64
dtype: object

In [15]:
address = 'Calgary, Alberta'

geolocator = Nominatim(user_agent="cal_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Calgary are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Calgary are 51.0534234, -114.0625892.


In [16]:
# create map of New York using latitude and longitude values
map_calgary = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, quadrant, neighborhood in zip(calgary_res['Latitude'], calgary_res['Longitude'], calgary_res['Quadrant'], calgary_res['Neighborhood']):
    label = '{}, {}'.format(neighborhood, quadrant)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_calgary)  
    
map_calgary

In [17]:
CLIENT_ID = 'TVGTHY4M2H3B3DOEUVJ2DXKYTSHBN1GDZ0YMRMX3CE2QV113' 
CLIENT_SECRET = '42KPMS5QLOTOG1SBLT3DLFQWX2WCWDLGD5DGVIIGCPO1Z3QZ' 
VERSION = '20190417' 
LIMIT = 100 
radius = 500 


print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: TVGTHY4M2H3B3DOEUVJ2DXKYTSHBN1GDZ0YMRMX3CE2QV113
CLIENT_SECRET:42KPMS5QLOTOG1SBLT3DLFQWX2WCWDLGD5DGVIIGCPO1Z3QZ


In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [19]:
calgary_venues = getNearbyVenues(names=calgary_res['Neighborhood'], 
                                 latitudes=calgary_res['Latitude'], 
                                 longitudes=calgary_res['Longitude']
                                )

Abbeydale
Acadia
Albert Park/Radisson Heights
Altadore
Applewood Park
Arbour Lake
Aspen Woods
Auburn Bay
Banff Trail
Bankview
Bayview
Beddington Heights
Bel-Aire
Beltline
Bonavista Downs
Bowness
Braeside
Brentwood
Bridgeland/Riverside
Bridlewood
Britannia
Cambrian Heights
Canyon Meadows
Capitol Hill
Castleridge
Cedarbrae
CFB Currie
CFB Lincoln Park PMQ
Chaparral
Charleswood
Chinatown
Chinook Park
Christie Park
Citadel
Cliff Bungalow
Coach Hill
Collingwood
Copperfield
Coral Springs
Cougar Ridge
Country Hills
Country Hills Village
Coventry Hills
Cranston
Crescent Heights
Crestmont
Dalhousie
Deer Ridge
Deer Run
Diamond Cove
Discovery Ridge
Douglasdale/Glen
Dover
Downtown Commercial Core
Downtown East Village
Downtown West End
Eagle Ridge
Eau Claire
Edgemont
Elbow Park
Elboya
Erin Woods
Erlton
Evanston
Evergreen
Fairview
Falconridge
Forest Heights
Forest Lawn
Glamorgan
Glenbrook
Glendale
Greenview
Greenwood/Greenbriar
Hamptons
Harvest Hills
Hawkwood
Haysboro
Hidden Valley
Highland Park
Hig

In [20]:
calgary_venues.shape

(1336, 7)

In [21]:
calgary_venues

Neighborhood  Neighborhood Latitude  \
0                         Abbeydale              51.059760   
1                            Acadia              50.972270   
2                            Acadia              50.972270   
3                            Acadia              50.972270   
4      Albert Park/Radisson Heights              51.042000   
5                          Altadore              51.016010   
6                          Altadore              51.016010   
7                          Altadore              51.016010   
8                    Applewood Park              51.045440   
9                    Applewood Park              51.045440   
10                      Arbour Lake              51.133510   
11                      Arbour Lake              51.133510   
12                      Arbour Lake              51.133510   
13                      Arbour Lake              51.133510   
14                      Aspen Woods              51.045190   
15                      Aspen Woods              51.045190   
16                      Aspen Woods              51.045190   
17                      Aspen Woods              51.045190   
18                      Aspen Woods              51.045190   
19                      Aspen Woods              51.045190   
20                      Aspen Woods              51.045190   
21                      Aspen Woods              51.045190   
22                       Auburn Bay              50.889760   
23                       Auburn Bay              50.889760   
24                       Auburn Bay              50.889760   
25                      Banff Trail              51.074720   
26                      Banff Trail              51.074720   
27                      Banff Trail              51.074720   
28                      Banff Trail              51.074720   
29                      Banff Trail              51.074720   
30                      Banff Trail              51.074720   
31                         Bankview              51.034120   
32                         Bankview              51.034120   
33                         Bankview              51.034120   
34                         Bankview              51.034120   
35               Beddington Heights              51.130900   
36               Beddington Heights              51.130900   
37                         Bel-Aire              50.999630   
38                         Bel-Aire              50.999630   
39                         Beltline              51.041610   
40                         Beltline              51.041610   
41                         Beltline              51.041610   
42                         Beltline              51.041610   
43                         Beltline              51.041610   
44                         Beltline              51.041610   
45                         Beltline              51.041610   
46                         Beltline              51.041610   
47                         Beltline              51.041610   
48                         Beltline              51.041610   
49                         Beltline              51.041610   
50                         Beltline              51.041610   
51                         Beltline              51.041610   
52                         Beltline              51.041610   
53                         Beltline              51.041610   
54                         Beltline              51.041610   
55                         Beltline              51.041610   
56                         Beltline              51.041610   
57                         Beltline              51.041610   
58                         Beltline              51.041610   
59                         Beltline              51.041610   
60                         Beltline              51.041610   
61                         Beltline              51.041610   
62                         Beltline              51.041610   
63                         Beltline              51.041

In [22]:
calgary_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                   
Abbeydale                                          1                       1   
Acadia                                             3                       3   
Albert Park/Radisson Heights                       1                       1   
Altadore                                           3                       3   
Applewood Park                                     2                       2   
Arbour Lake                                        4                       4   
Aspen Woods                                        8                       8   
Auburn Bay                                         3                       3   
Banff Trail                                        6                       6   
Bankview                                           4                       4   
Beddington Heights                                 2                       2   
Bel-Aire                                           2                       2   
Beltline                                          65                      65   
Bonavista Downs                                    4                       4   
Bowness                                            5                       5   
Braeside                                           6                       6   
Brentwood                                          5                       5   
Bridgeland/Riverside                              26                      26   
Bridlewood                                         2                       2   
Britannia                                          1                       1   
CFB Currie                                        56                      56   
CFB Lincoln Park PMQ                               5                       5   
Cambrian Heights                                   1                       1   
Canyon Meadows                                     4                       4   
Capitol Hill                                       5                       5   
Cedarbrae                                          4                       4   
Chaparral                                          4                       4   
Charleswood                                        4                       4   
Chinatown                                          7                       7   
Chinook Park                                       3                       3   
Christie Park                                      2                       2   
Citadel                                            1                       1   
Cliff Bungalow                                    36                      36   
Coach Hill                                         4                       4   
Collingwood                                        5                       5   
Copperfield                                        5                       5   
Coral Springs                                      1                       1   
Cougar Ridge                                       3                       3   
Country Hills                                     16                      16   
Country Hills Village                             16                      16   
Coventry Hills                                     2                       2   
Cranston                                          10                      10   
Crescent Heights                                  13                      13   
Crestmont                                          2                       2   
Dalhousie                                          2                       2   
Deer Ridge                                         2                       2   
Deer Run                                           3                       3   
Diamond Cove                                       1                       1   
Discovery Ridge                

In [23]:
print('There are {} uniques categories.'.format(len(calgary_venues['Venue Category'].unique())))

There are 216 uniques categories.


In [24]:
# one hot encoding
calgary_onehot = pd.get_dummies(calgary_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
calgary_onehot['Neighborhood'] = calgary_venues['Neighborhood'] 

calgary_onehot.head()

ATM  Accessories Store  Adult Boutique  Airport Service  \
0    0                  0               0                0   
1    0                  0               0                0   
2    0                  0               0                0   
3    0                  0               0                0   
4    0                  0               0                0   

   American Restaurant  Argentinian Restaurant  Art Gallery  \
0                    0                       0            0   
1                    0                       0            0   
2                    0                       0            0   
3                    0                       0            0   
4                    0                       0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Automotive Shop  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   BBQ Joint  Bakery  Bank  Bar  Baseball Field  Beach  Beer Bar  Beer Garden  \
0          0       0     0    0               0      0         0            0   
1          0       0     0    0               0      0         0            0   
2          0       0     0    0               0      0         0            0   
3          0       0     0    0               0      0         0            0   
4          0       0     0    0               0      0         0            0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0           0              0          0         0              0   
1           0              0          0         0              0   
2           0              0          0         0              0   
3           0              0          0         0              0   
4           0              0          0         0              0   

   Bowling Green  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0                     0               0        0   
1              0                     0               0        0   
2              0                     0               0        0   
3              0                     0               0        0   
4              0                     0               0        0   

   Bubble Tea Shop  Building  Burger Joint  Bus Station  Bus Stop  \
0                0         0             0            0         0   
1                0         0             0            0         0   
2                0         0             0            0         0   
3                0         0             0            0         0   
4                0         0             0            0         0   

   Business Service  Café  Camera Store  Candy Store  Chinese Restaurant  \
0                 0     0             0            0                   0   
1                 0     0             0            0                   0   
2                 0     0             0            0                   0   
3                 0     0             0            0                   0   
4                 0     0             0            0                   0   

   Chocolate Shop  Clothing Store  Cocktail Bar  Coffee Shop  College Gym  \
0               0               0             0            0            0   
1               0               0             0            0            0   
2               0               0             0            0            0   
3               0               0             0            0            0   
4               0               0             0            0            0   

   Comic Shop  Concert Hall  Construction & Landscaping  Convenience Store  \
0           0             0                         

In [25]:
calgary_onehot.shape

(1336, 216)

In [26]:
cols = ['Neighborhood']
calgary_onehot = calgary_onehot[[c for c in cols if c in calgary_onehot] + [c for c in calgary_onehot if c not in cols]]

In [27]:
calgary_onehot.head()

Neighborhood  ATM  Accessories Store  Adult Boutique  \
0                     Abbeydale    0                  0               0   
1                        Acadia    0                  0               0   
2                        Acadia    0                  0               0   
3                        Acadia    0                  0               0   
4  Albert Park/Radisson Heights    0                  0               0   

   Airport Service  American Restaurant  Argentinian Restaurant  Art Gallery  \
0                0                    0                       0            0   
1                0                    0                       0            0   
2                0                    0                       0            0   
3                0                    0                       0            0   
4                0                    0                       0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Automotive Shop  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   BBQ Joint  Bakery  Bank  Bar  Baseball Field  Beach  Beer Bar  Beer Garden  \
0          0       0     0    0               0      0         0            0   
1          0       0     0    0               0      0         0            0   
2          0       0     0    0               0      0         0            0   
3          0       0     0    0               0      0         0            0   
4          0       0     0    0               0      0         0            0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0           0              0          0         0              0   
1           0              0          0         0              0   
2           0              0          0         0              0   
3           0              0          0         0              0   
4           0              0          0         0              0   

   Bowling Green  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0                     0               0        0   
1              0                     0               0        0   
2              0                     0               0        0   
3              0                     0               0        0   
4              0                     0               0        0   

   Bubble Tea Shop  Building  Burger Joint  Bus Station  Bus Stop  \
0                0         0             0            0         0   
1                0         0             0            0         0   
2                0         0             0            0         0   
3                0         0             0            0         0   
4                0         0             0            0         0   

   Business Service  Café  Camera Store  Candy Store  Chinese Restaurant  \
0                 0     0             0            0                   0   
1                 0     0             0            0                   0   
2                 0     0             0            0                   0   
3                 0     0             0            0                   0   
4                 0     0             0            0                   0   

   Chocolate Shop  Clothing Store  Cocktail Bar  Coffee Shop  College Gym  \
0               0               0             0            0            0   
1               0               0             0            0            0   
2               0               0             0            0            0   
3               0               0             0            0            0   
4               0               0           

In [28]:
calgary_onehot.shape

(1336, 216)

In [29]:
calgary_grouped = calgary_onehot.groupby('Neighborhood').mean().reset_index()
calgary_grouped

Neighborhood   ATM  Accessories Store  Adult Boutique  \
0                        Abbeydale  0.00           0.000000            0.00   
1                           Acadia  0.00           0.000000            0.00   
2     Albert Park/Radisson Heights  0.00           0.000000            0.00   
3                         Altadore  0.00           0.000000            0.00   
4                   Applewood Park  0.00           0.000000            0.00   
5                      Arbour Lake  0.00           0.000000            0.00   
6                      Aspen Woods  0.00           0.000000            0.00   
7                       Auburn Bay  0.00           0.000000            0.00   
8                      Banff Trail  0.00           0.000000            0.00   
9                         Bankview  0.00           0.000000            0.00   
10              Beddington Heights  0.00           0.000000            0.00   
11                        Bel-Aire  0.00           0.000000            0.00   
12                        Beltline  0.00           0.000000            0.00   
13                 Bonavista Downs  0.00           0.000000            0.00   
14                         Bowness  0.00           0.000000            0.00   
15                        Braeside  0.00           0.000000            0.00   
16                       Brentwood  0.00           0.000000            0.00   
17            Bridgeland/Riverside  0.00           0.000000            0.00   
18                      Bridlewood  0.00           0.000000            0.00   
19                       Britannia  0.00           0.000000            0.00   
20                      CFB Currie  0.00           0.000000            0.00   
21            CFB Lincoln Park PMQ  0.00           0.000000            0.00   
22                Cambrian Heights  0.00           0.000000            0.00   
23                  Canyon Meadows  0.00           0.000000            0.00   
24                    Capitol Hill  0.00           0.000000            0.00   
25                       Cedarbrae  0.00           0.000000            0.00   
26                       Chaparral  0.00           0.000000            0.00   
27                     Charleswood  0.00           0.000000            0.00   
28                       Chinatown  0.00           0.000000            0.00   
29                    Chinook Park  0.00           0.000000            0.00   
30                   Christie Park  0.00           0.000000            0.00   
31                         Citadel  0.00           0.000000            0.00   
32                  Cliff Bungalow  0.00           0.000000            0.00   
33                      Coach Hill  0.00           0.000000            0.00   
34                     Collingwood  0.00           0.000000            0.00   
35                     Copperfield  0.00           0.000000            0.00   
36                   Coral Springs  0.00           0.000000            0.00   
37                    Cougar Ridge  0.00           0.000000            0.00   
38                   Country Hills  0.00           0.000000            0.00   
39           Country Hills Village  0.00           0.000000            0.00   
40                  Coventry Hills  0.00           0.000000            0.00   
41                        Cranston  0.00           0.000000            0.00   
42                Crescent Heights  0.00           0.000000            0.00   
43                       Crestmont  0.00           0.000000            0.00   
44                       Dalhousie  0.00           0.000000            0.00   
45                      Deer Ridge  0.00           0.000000            0.00   
46                        Deer Run  0.00           0.000000            0.00   
47                    Diamond Cove  0.00           0.000000            0.00   
48                 Discovery Ridge  0.00           0.000000            0.00   
49                Douglasdale/Glen  0.00           0.000000            0

In [30]:
calgary_grouped.shape

(183, 216)

In [31]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [32]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = calgary_grouped['Neighborhood']

for ind in np.arange(calgary_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(calgary_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood                     1st Most Common Venue  \
0                        Abbeydale                   Health & Beauty Service   
1                           Acadia                         Recreation Center   
2     Albert Park/Radisson Heights                                 Rock Club   
3                         Altadore                            Ice Cream Shop   
4                   Applewood Park                                     Trail   
5                      Arbour Lake  Residential Building (Apartment / Condo)   
6                      Aspen Woods                               Coffee Shop   
7                       Auburn Bay                                      Park   
8                      Banff Trail                                       Inn   
9                         Bankview                               Pizza Place   
10              Beddington Heights                                   Theater   
11                        Bel-Aire                            Scenic Lookout   
12                        Beltline                               Coffee Shop   
13                 Bonavista Downs                                 BBQ Joint   
14                         Bowness                                       Pub   
15                        Braeside                                       Pub   
16                       Brentwood                              Dance Studio   
17            Bridgeland/Riverside                               Pizza Place   
18                      Bridlewood                Construction & Landscaping   
19                       Britannia                               Coffee Shop   
20                      CFB Currie                                     Hotel   
21            CFB Lincoln Park PMQ                            Breakfast Spot   
22                Cambrian Heights                                Restaurant   
23                  Canyon Meadows                                       Spa   
24                    Capitol Hill                             Jewelry Store   
25                       Cedarbrae                     Vietnamese Restaurant   
26                       Chaparral                           Airport Service   
27                     Charleswood                       Sporting Goods Shop   
28                       Chinatown                                      Park   
29                    Chinook Park                                      Café   
30                   Christie Park                            Massage Studio   
31                         Citadel                          Business Service   
32                  Cliff Bungalow                               Pizza Place   
33                      Coach Hill                               Gas Station   
34                     Collingwood                                       Pub   
35                     Copperfield                                Playground   
36                   Coral Springs                                     Beach   
37                    Cougar Ridge                            Cosmetics Shop   
38                   Country Hills                               Gas Station   
39           Country Hills Village                      Fast Food Restaurant   
40                  Coventry Hills                                Playground   
41                        Cranston                                      Café   
42                Crescent Heights                            Scenic Lookout   
43                       Crestmont                                Playground   
44                       Dalhousie                               Music Venue   
45                      Deer Ridge                                       Spa   
46                        Deer Run                                   Dog Run   
47                    Diamond Cove                  Mediterranean Restaurant   
48                 Discovery Ridge                            Cosmetics Shop   
49                Doug

In [33]:
neighborhoods_venues_sorted.shape

(183, 11)

In [34]:
# set number of clusters
kclusters = 6

calgary_grouped_clustering = calgary_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(calgary_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:183] 

array([3, 3, 3, 1, 1, 3, 3, 1, 3, 0, 3, 3, 3, 3, 3, 0, 0, 3, 2, 3, 3, 3,
       3, 0, 3, 3, 3, 3, 3, 3, 1, 5, 3, 0, 0, 0, 3, 3, 3, 3, 4, 3, 3, 4,
       3, 3, 3, 3, 0, 0, 3, 3, 3, 3, 3, 3, 3, 1, 3, 1, 1, 2, 3, 3, 3, 0,
       3, 0, 0, 0, 3, 1, 3, 0, 3, 0, 3, 3, 3, 3, 3, 3, 0, 0, 3, 3, 3, 3,
       5, 3, 2, 3, 3, 3, 3, 4, 3, 3, 3, 1, 3, 3, 3, 1, 3, 3, 3, 3, 4, 3,
       3, 0, 1, 3, 3, 2, 0, 3, 3, 1, 0, 3, 3, 3, 5, 3, 3, 0, 3, 1, 0, 1,
       3, 3, 3, 3, 3, 1, 0, 3, 2, 2, 0, 1, 3, 3, 1, 5, 1, 2, 0, 0, 3, 3,
       3, 3, 3, 3, 3, 3, 3, 1, 2, 2, 3, 3, 3, 3, 3, 1, 0, 0, 3, 3, 0, 3,
       0, 1, 3, 3, 3, 3, 3])

In [35]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [42]:
neighborhoods_venues_sorted.shape

(183, 12)

In [40]:
calgary_merged = calgary_res
calgary_merged

Neighborhood Quadrant     Sector  Ward         Type  \
0                        Abbeydale    NE/SE  Northeast    10  Residential   
1                           Acadia       SE      South     9  Residential   
2     Albert Park/Radisson Heights       SE       East    10  Residential   
3                         Altadore       SW     Centre    11  Residential   
4                   Applewood Park    SE/NE       East    10  Residential   
5                      Arbour Lake       NW  Northwest     2  Residential   
6                      Aspen Woods       SW       West     6  Residential   
7                       Auburn Bay       SE  Southeast    12  Residential   
8                      Banff Trail       NW     Centre     7  Residential   
9                         Bankview       SW     Centre     8  Residential   
10                         Bayview       SW      South    11  Residential   
11              Beddington Heights    NW/NE      North     4  Residential   
12                        Bel-Aire       SW     Centre    11  Residential   
13                        Beltline    SW/SE     Centre     8  Residential   
14                 Bonavista Downs       SE      South    14  Residential   
15                         Bowness       NW  Northwest     1  Residential   
16                        Braeside       SW      South    11  Residential   
17                       Brentwood       NW  Northwest     7  Residential   
18            Bridgeland/Riverside    NE/SE     Centre   7/9  Residential   
19                      Bridlewood       SW      South    13  Residential   
20                       Britannia       SW     Centre    11  Residential   
21                Cambrian Heights       NW     Centre     7  Residential   
22                  Canyon Meadows       SW      South    13  Residential   
23                    Capitol Hill       NW     Centre     7  Residential   
24                     Castleridge       NE  Northeast     5  Residential   
25                       Cedarbrae       SW      South    11  Residential   
26                      CFB Currie       SW       West    11  Residential   
27            CFB Lincoln Park PMQ       SW       West    11  Residential   
28                       Chaparral       SE      South    14  Residential   
29                     Charleswood       NW  Northwest     7  Residential   
30                       Chinatown    SW/SE     Centre     7  Residential   
31                    Chinook Park       SW      South    11  Residential   
32                   Christie Park       SW       West     6  Residential   
33                         Citadel       NW  Northwest     2  Residential   
34                  Cliff Bungalow       SW     Centre     8  Residential   
35                      Coach Hill       SW       West     6  Residential   
36                     Collingwood       NW  Northwest     7  Residential   
37                     Copperfield       SE  Southeast    12  Residential   
38                   Coral Springs       NE  Northeast     5  Residential   
39                    Cougar Ridge       SW       West     6  Residential   
40                   Country Hills       NW      North     4  Residential   
41           Country Hills Village       NE      North     3  Residential   
42                  Coventry Hills       NE      North     3  Residential   
43                        Cranston       SE  Southeast    12  Residential   
44                Crescent Heights    NE/NW     Centre     7  Residential   
45                       Crestmont       SW       West     1  Residential   
46                       Dalhousie       NW  Northwest     7  Residential   
47                      Deer Ridge       SE      South    14  Residential   
48                        Deer Run       SE      South    14  Residential   
49                    Diamond Cove       SE      South    14  Residential   
50                 Discovery Ridge       SW       West     6  Residential   
51                

In [44]:
calgary_merged = calgary_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

In [45]:
calgary_merged

Neighborhood Quadrant     Sector  Ward         Type  \
0                        Abbeydale    NE/SE  Northeast    10  Residential   
1                           Acadia       SE      South     9  Residential   
2     Albert Park/Radisson Heights       SE       East    10  Residential   
3                         Altadore       SW     Centre    11  Residential   
4                   Applewood Park    SE/NE       East    10  Residential   
5                      Arbour Lake       NW  Northwest     2  Residential   
6                      Aspen Woods       SW       West     6  Residential   
7                       Auburn Bay       SE  Southeast    12  Residential   
8                      Banff Trail       NW     Centre     7  Residential   
9                         Bankview       SW     Centre     8  Residential   
10                         Bayview       SW      South    11  Residential   
11              Beddington Heights    NW/NE      North     4  Residential   
12                        Bel-Aire       SW     Centre    11  Residential   
13                        Beltline    SW/SE     Centre     8  Residential   
14                 Bonavista Downs       SE      South    14  Residential   
15                         Bowness       NW  Northwest     1  Residential   
16                        Braeside       SW      South    11  Residential   
17                       Brentwood       NW  Northwest     7  Residential   
18            Bridgeland/Riverside    NE/SE     Centre   7/9  Residential   
19                      Bridlewood       SW      South    13  Residential   
20                       Britannia       SW     Centre    11  Residential   
21                Cambrian Heights       NW     Centre     7  Residential   
22                  Canyon Meadows       SW      South    13  Residential   
23                    Capitol Hill       NW     Centre     7  Residential   
24                     Castleridge       NE  Northeast     5  Residential   
25                       Cedarbrae       SW      South    11  Residential   
26                      CFB Currie       SW       West    11  Residential   
27            CFB Lincoln Park PMQ       SW       West    11  Residential   
28                       Chaparral       SE      South    14  Residential   
29                     Charleswood       NW  Northwest     7  Residential   
30                       Chinatown    SW/SE     Centre     7  Residential   
31                    Chinook Park       SW      South    11  Residential   
32                   Christie Park       SW       West     6  Residential   
33                         Citadel       NW  Northwest     2  Residential   
34                  Cliff Bungalow       SW     Centre     8  Residential   
35                      Coach Hill       SW       West     6  Residential   
36                     Collingwood       NW  Northwest     7  Residential   
37                     Copperfield       SE  Southeast    12  Residential   
38                   Coral Springs       NE  Northeast     5  Residential   
39                    Cougar Ridge       SW       West     6  Residential   
40                   Country Hills       NW      North     4  Residential   
41           Country Hills Village       NE      North     3  Residential   
42                  Coventry Hills       NE      North     3  Residential   
43                        Cranston       SE  Southeast    12  Residential   
44                Crescent Heights    NE/NW     Centre     7  Residential   
45                       Crestmont       SW       West     1  Residential   
46                       Dalhousie       NW  Northwest     7  Residential   
47                      Deer Ridge       SE      South    14  Residential   
48                        Deer Run       SE      South    14  Residential   
49                    Diamond Cove       SE      South    14  Residential   
50                 Discovery Ridge       SW       West     6  Residential   
51                

In [46]:
calgary_mergedd = calgary_merged.dropna(subset=['Cluster Labels'])

In [47]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(calgary_mergedd['Latitude'], calgary_mergedd['Longitude'], calgary_mergedd['Neighborhood'], calgary_mergedd['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [77]:
rows = calgary_mergedd['Cluster Labels'] == 0
columns = ['Neighborhood', 'Cluster Labels', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue']
calgary_mergedd.loc[rows, columns]

Neighborhood  Cluster Labels 1st Most Common Venue  \
9               Bankview             0.0           Pizza Place   
16              Braeside             0.0                   Pub   
17             Brentwood             0.0          Dance Studio   
22        Canyon Meadows             0.0                   Spa   
35            Coach Hill             0.0           Gas Station   
36           Collingwood             0.0                   Pub   
37           Copperfield             0.0            Playground   
50       Discovery Ridge             0.0        Cosmetics Shop   
51      Douglasdale/Glen             0.0           Gas Station   
67        Forest Heights             0.0                  Bank   
69             Glamorgan             0.0           Pizza Place   
70             Glenbrook             0.0          Intersection   
71              Glendale             0.0           Pizza Place   
76              Hawkwood             0.0           Gas Station   
78         Hidden Valley             0.0           Pizza Place   
85          Kelvin Grove             0.0     Convenience Store   
86   Killarney/Glengarry             0.0                School   
115          North Haven             0.0            Playground   
120       Panorama Hills             0.0           Pizza Place   
124            Patterson             0.0                   Bar   
132           Ranchlands             0.0           Pizza Place   
136             Richmond             0.0           Pizza Place   
145               Rundle             0.0                   Pub   
149     Sandstone Valley             0.0         Design Studio   
161        Skyview Ranch             0.0           Gas Station   
162             Somerset             0.0          Burger Joint   
181         Valley Ridge             0.0           Golf Course   
182              Varsity             0.0           Pizza Place   
185       West Hillhurst             0.0    Italian Restaurant   
188            Whitehorn             0.0           Gas Station   

     2nd Most Common Venue       3rd Most Common Venue  \
9              Coffee Shop                 Candy Store   
16          Ice Cream Shop                 Pizza Place   
17             Pizza Place           Convenience Store   
22             Pizza Place  Construction & Landscaping   
35   Vietnamese Restaurant                 Pizza Place   
36            Burger Joint           Convenience Store   
37            Dance Studio           Convenience Store   
50       Convenience Store                 Yoga Studio   
51            Optical Shop                 Pizza Place   
67       Convenience Store                 Yoga Studio   
69      Salon / Barbershop            Sushi Restaurant   
70        Business Service           Convenience Store   
71                Bus Stop  Construction & Landscaping   
76             Pizza Place           Convenience Store   
78            Intersection                 Gas Station   
85             Yoga Studio                 Film Studio   
86       Convenience Store                    Pharmacy   
115            Pizza Place              Scenic Lookout   
120            Yoga Studio                 Film Studio   
124            Gas Station       Vietnamese Restaurant   
132      Convenience Store               Boat or Ferry   
136             Playground                 Coffee Shop   
145       Business Service           Convenience Store   
149       Business Service                 Pizza Place   
161            Pizza Place        Fast Food Restaurant   
162                  Plaza                 Bus Station   
181             Restaurant            Greek Restaurant   
182            Yoga Studio                 Gas Station   
185            Pizza Place                   Gift Shop   
188            Pizza Place        Medical Supply Store   

          4th Most Common Venue    5th Most Common Venue  \
9                   Film Studio              Gas Station   
16            Convenience Store               

In [76]:
rows = calgary_mergedd['Cluster Labels'] == 1
columns = ['Neighborhood', 'Cluster Labels', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue']
calgary_mergedd.loc[rows, columns]

Neighborhood  Cluster Labels 1st Most Common Venue  \
3             Altadore             1.0        Ice Cream Shop   
4       Applewood Park             1.0                 Trail   
7           Auburn Bay             1.0                  Park   
32       Christie Park             1.0        Massage Studio   
59          Elbow Park             1.0   Japanese Restaurant   
61          Erin Woods             1.0                  Park   
62              Erlton             1.0                  Park   
74            Hamptons             1.0                  Park   
103      McKenzie Lake             1.0                  Park   
107           Millrise             1.0                  Park   
116  North Haven Upper             1.0         Moving Target   
123           Parkland             1.0                  Park   
135            Renfrew             1.0        Breakfast Spot   
137        Rideau Park             1.0                  Park   
143            Roxboro             1.0                  Park   
152       Scenic Acres             1.0        Massage Studio   
157           Sherwood             1.0                  Park   
159     Silver Springs             1.0                  Park   
172          Sunnyside             1.0                  Park   
180  Upper Mount Royal             1.0                  Park   
189           Wildwood             1.0                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3                     Pub                  Park           Yoga Studio   
4                    Park           Yoga Studio           Film Studio   
7             Bus Station            Playground           Yoga Studio   
32                   Park           Yoga Studio     Food & Drink Shop   
59                  River     Health Food Store                  Park   
61            Yoga Studio     Food & Drink Shop             Gastropub   
62         Breakfast Spot        History Museum            Playground   
74            Golf Course        Baseball Field             Gift Shop   
103           Yoga Studio     Food & Drink Shop             Gastropub   
107           Golf Course            Playground          Skating Rink   
116           Coffee Shop                  Park     Food & Drink Shop   
123                Garden           Yoga Studio     Food & Drink Shop   
135                  Park  Gym / Fitness Center             Gastropub   
137           Supermarket                  Café                 Trail   
143                  Café                 Trail           Yoga Studio   
152                  Park           Yoga Studio     Food & Drink Shop   
157           Yoga Studio     Food & Drink Shop             Gastropub   
159                   Gym        Baseball Field             Gift Shop   
172        Scenic Lookout          Skating Rink            Restaurant   
180                 River    Athletics & Sports           Yoga Studio   
189               Dog Run                 Trail           Yoga Studio   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3             Film Studio                Garden           Gaming Cafe   
4             Gas Station                Garden           Gaming Cafe   
7             Gas Station                Garden           Gaming Cafe   
32            Gas Station                Garden           Gaming Cafe   
59            Yoga Studio           Film Studio                Garden   
61            Gas Station                Garden           Gaming Cafe   
62     Light Rail Station           Gas Station                Garden   
74              Gastropub           Gas Station                Garden   
103           Gas Station                Garden           Gaming Cafe   
107           Film Studio                Garden           Gaming Cafe   
116             Gastropub           Gas Station                Garden   
123             Gastropub           Gas Station           Gaming Cafe   
135           Gas Station                Gard

In [75]:
rows = calgary_mergedd['Cluster Labels'] == 2
columns = ['Neighborhood', 'Cluster Labels', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue']
calgary_mergedd.loc[rows, columns]

Neighborhood  Cluster Labels       1st Most Common Venue  \
19     Bridlewood             2.0  Construction & Landscaping   
63       Evanston             2.0                  Playground   
94   MacEwan Glen             2.0                Home Service   
119      Palliser             2.0              Cosmetics Shop   
147  Saddle Ridge             2.0                Home Service   
148     Sage Hill             2.0                    Pharmacy   
160     Silverado             2.0                 Bus Station   
173      Taradale             2.0                     Dog Run   
174        Temple             2.0                Home Service   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
19           Home Service           Yoga Studio           Film Studio   
63           Home Service            Print Shop          Soccer Field   
94                   Park           Yoga Studio           Film Studio   
119            Playground          Home Service           Yoga Studio   
147           Yoga Studio           Film Studio             Gastropub   
148          Home Service   Filipino Restaurant           Gas Station   
160          Home Service    Photography Studio           Yoga Studio   
173                  Lake          Home Service           Yoga Studio   
174           Yoga Studio           Film Studio             Gastropub   

    5th Most Common Venue 6th Most Common Venue   7th Most Common Venue  \
19            Gas Station                Garden             Gaming Cafe   
63                   Park           Yoga Studio     Filipino Restaurant   
94            Gas Station                Garden             Gaming Cafe   
119           Film Studio           Gas Station                  Garden   
147           Gas Station                Garden             Gaming Cafe   
148                Garden           Gaming Cafe  Furniture / Home Store   
160     Food & Drink Shop           Gas Station                  Garden   
173     Food & Drink Shop             Gastropub             Gas Station   
174           Gas Station                Garden             Gaming Cafe   

      8th Most Common Venue   9th Most Common Venue  10th Most Common Venue  
19   Furniture / Home Store      Frozen Yogurt Shop     Fried Chicken Joint  
63              Gaming Cafe  Furniture / Home Store      Frozen Yogurt Shop  
94   Furniture / Home Store      Frozen Yogurt Shop     Fried Chicken Joint  
119             Gaming Cafe  Furniture / Home Store      Frozen Yogurt Shop  
147  Furniture / Home Store      Frozen Yogurt Shop     Fried Chicken Joint  
148      Frozen Yogurt Shop     Fried Chicken Joint       French Restaurant  
160             Gaming Cafe  Furniture / Home Store      Frozen Yogurt Shop  
173                  Garden             Gaming Cafe  Furniture / Home Store  
174  Furniture / Home Store      Frozen Yogurt Shop     Fried Chicken Joint

In [74]:
rows = calgary_mergedd['Cluster Labels'] == 3
columns = ['Neighborhood', 'Cluster Labels', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue']
calgary_mergedd.loc[rows, columns]

Neighborhood  Cluster Labels  \
0                        Abbeydale             3.0   
1                           Acadia             3.0   
2     Albert Park/Radisson Heights             3.0   
5                      Arbour Lake             3.0   
6                      Aspen Woods             3.0   
8                      Banff Trail             3.0   
11              Beddington Heights             3.0   
12                        Bel-Aire             3.0   
13                        Beltline             3.0   
14                 Bonavista Downs             3.0   
15                         Bowness             3.0   
18            Bridgeland/Riverside             3.0   
20                       Britannia             3.0   
21                Cambrian Heights             3.0   
23                    Capitol Hill             3.0   
25                       Cedarbrae             3.0   
26                      CFB Currie             3.0   
27            CFB Lincoln Park PMQ             3.0   
28                       Chaparral             3.0   
29                     Charleswood             3.0   
30                       Chinatown             3.0   
31                    Chinook Park             3.0   
34                  Cliff Bungalow             3.0   
38                   Coral Springs             3.0   
39                    Cougar Ridge             3.0   
40                   Country Hills             3.0   
41           Country Hills Village             3.0   
43                        Cranston             3.0   
44                Crescent Heights             3.0   
46                       Dalhousie             3.0   
47                      Deer Ridge             3.0   
48                        Deer Run             3.0   
49                    Diamond Cove             3.0   
52                           Dover             3.0   
53        Downtown Commercial Core             3.0   
54           Downtown East Village             3.0   
55               Downtown West End             3.0   
56                     Eagle Ridge             3.0   
57                      Eau Claire             3.0   
58                        Edgemont             3.0   
60                          Elboya             3.0   
64                       Evergreen             3.0   
65                        Fairview             3.0   
66                     Falconridge             3.0   
68                     Forest Lawn             3.0   
72                       Greenview             3.0   
75                   Harvest Hills             3.0   
77                        Haysboro             3.0   
79                   Highland Park             3.0   
80                        Highwood             3.0   
81                       Hillhurst             3.0   
82   Hounsfield Heights/Briar Hill             3.0   
83                Huntington Hills             3.0   
84                       Inglewood             3.0   
87                         Kincora             3.0   
88                       Kingsland             3.0   
89                  Lake Bonavista             3.0   
90                        Lakeview             3.0   
92                    Lincoln Park             3.0   
95                        Mahogany             3.0   
96                      Manchester             3.0   
97                     Maple Ridge             3.0   
98                     Marlborough             3.0   
100                     Martindale             3.0   
101                        Mayfair             3.0   
102                Mayland Heights             3.0   
104                 McKenzie Towne             3.0   
105                Meadowlark Park             3.0   
106                      Midnapore             3.0   
108                        Mission             3.0   
109                  Monterey Park             3.0   
110                     Montgomery             3.0   
111                 Mount Pleasant             3.0   
113                     No

In [73]:
rows = calgary_mergedd['Cluster Labels'] == 4
columns = ['Neighborhood', 'Cluster Labels', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue']
calgary_mergedd.loc[rows, columns]

Neighborhood  Cluster Labels 1st Most Common Venue  \
42     Coventry Hills             4.0            Playground   
45          Crestmont             4.0            Playground   
99   Marlborough Park             4.0            Playground   
112      New Brighton             4.0            Playground   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
42             Smoke Shop           Yoga Studio           Film Studio   
45            Yoga Studio           Film Studio             Gastropub   
99            Yoga Studio           Film Studio             Gastropub   
112           Yoga Studio           Film Studio             Gastropub   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
42            Gas Station                Garden           Gaming Cafe   
45            Gas Station                Garden           Gaming Cafe   
99            Gas Station                Garden           Gaming Cafe   
112           Gas Station                Garden           Gaming Cafe   

      8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
42   Furniture / Home Store    Frozen Yogurt Shop    Fried Chicken Joint  
45   Furniture / Home Store    Frozen Yogurt Shop    Fried Chicken Joint  
99   Furniture / Home Store    Frozen Yogurt Shop    Fried Chicken Joint  
112  Furniture / Home Store    Frozen Yogurt Shop    Fried Chicken Joint

In [72]:
rows = calgary_mergedd['Cluster Labels'] == 5
columns = ['Neighborhood', 'Cluster Labels', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue',
       '6th Most Common Venue', '7th Most Common Venue',
       '8th Most Common Venue', '9th Most Common Venue',
       '10th Most Common Venue']
calgary_mergedd.loc[rows, columns]

Neighborhood  Cluster Labels 1st Most Common Venue  \
33               Citadel             5.0      Business Service   
91                Legacy             5.0      Business Service   
129  Queens Park Village             5.0             Wine Shop   
158          Signal Hill             5.0      Business Service   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
33            Yoga Studio     Food & Drink Shop             Gastropub   
91            Yoga Studio     Food & Drink Shop             Gastropub   
129      Business Service           Yoga Studio     Food & Drink Shop   
158           Yoga Studio     Food & Drink Shop             Gastropub   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
33            Gas Station                Garden           Gaming Cafe   
91            Gas Station                Garden           Gaming Cafe   
129             Gastropub           Gas Station                Garden   
158           Gas Station                Garden           Gaming Cafe   

      8th Most Common Venue   9th Most Common Venue 10th Most Common Venue  
33   Furniture / Home Store      Frozen Yogurt Shop    Fried Chicken Joint  
91   Furniture / Home Store      Frozen Yogurt Shop    Fried Chicken Joint  
129             Gaming Cafe  Furniture / Home Store     Frozen Yogurt Shop  
158  Furniture / Home Store      Frozen Yogurt Shop    Fried Chicken Joint